**IMDb의 영화 평점 예측 모델 만들기**

Kaggle 사이트에서 가져온 IMDb라는 영화 평점 사이트의 데이터를 이용해, feature를 분석하여 영화가 받게 될 평점을 예측하는 모델을 훈련하고자 합니다.

In [2]:
import numpy as np
import pandas as pd

from sklearn.model_selection import train_test_split

import io
from google.colab import files

In [3]:
myfile = files.upload()

Saving IMDb movies.csv to IMDb movies (1).csv
Saving IMDb ratings.csv to IMDb ratings (1).csv


In [4]:
movies = pd.read_csv(io.BytesIO(myfile['IMDb movies.csv']))
# names = pd.read_csv(io.BytesIO(myfile['IMDb names.csv']))
ratings = pd.read_csv(io.BytesIO(myfile['IMDb ratings.csv']))
# titles = pd.read_csv(io.BytesIO(myfile['IMDb title_principals.csv']))

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (3) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [16]:
# 글자 분석은 아직 배우지 않았으니, movies와 ratings 만을 이용하여 영화의 평점 예측 모델을 만들겠습니다.
# 공통 column은 imdb_title_id 입니다.
movierating = pd.merge(movies, ratings, how='outer',on='imdb_title_id')

In [6]:
movierating.columns

Index(['imdb_title_id', 'title', 'original_title', 'year', 'date_published',
       'genre', 'duration', 'country', 'language', 'director', 'writer',
       'production_company', 'actors', 'description', 'avg_vote', 'votes',
       'budget', 'usa_gross_income', 'worlwide_gross_income', 'metascore',
       'reviews_from_users', 'reviews_from_critics', 'weighted_average_vote',
       'total_votes', 'mean_vote', 'median_vote', 'votes_10', 'votes_9',
       'votes_8', 'votes_7', 'votes_6', 'votes_5', 'votes_4', 'votes_3',
       'votes_2', 'votes_1', 'allgenders_0age_avg_vote',
       'allgenders_0age_votes', 'allgenders_18age_avg_vote',
       'allgenders_18age_votes', 'allgenders_30age_avg_vote',
       'allgenders_30age_votes', 'allgenders_45age_avg_vote',
       'allgenders_45age_votes', 'males_allages_avg_vote',
       'males_allages_votes', 'males_0age_avg_vote', 'males_0age_votes',
       'males_18age_avg_vote', 'males_18age_votes', 'males_30age_avg_vote',
       'males_30age_votes'

In [7]:
# 우선 목표는 rating이므로, 위 column 중 weighted_average_vote(가중치를 둔 평균평점) 항목이 없는 영화는 삭제하기 위해 빈 칸이 있는지 확인합니다.
movierating['weighted_average_vote'].isna().sum()

0

In [8]:
# 없으므로, 8만개 넘는 영화 데이터 전부를 사용하겠습니다.

1. EDA
데이터를 모델에 넣기 위해 파일이 가지고 있는 column들을 분석해 일부 항목을 잘라내고 합치는 등의 분석을 수행합니다.

In [17]:
# 우선 중복된 column들을 없애겠습니다.
movierating = movierating.drop(['avg_vote', 'votes'], axis=1)

In [10]:
# 다음으로, 추가로 없앨 colum들을 살펴보겠습니다.

In [11]:
# pip install -U pandas-profiling

In [12]:
from pandas_profiling import ProfileReport
profile = ProfileReport(movierating, minimal=True).to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [13]:
# pandas profile을 볼 때, 우선 고유값이 너무 많은 다음의 column들은 삭제합니다.
# title, original_title = 영화 제목하고 평점이 관계가 있다고 보기 힘들고, 고유값이 데이터 크기만큼 많습니다. 
# director, writer, production_company = 감독, 작가 및 영화사도 고유값이 3만개(작가의 경우 6만개)가 넘으며, 평점과 영화사 등에 어느정도 관계는 있을수도 있겠으나 분석이 너무 오래 걸릴것으로 보입니다.
# actors = 데이터가 영화에 출연한 모든 배우를 나열하고 있어서, 고유값이 클 뿐더러 분석이 매우 힘듭니다.
# description = 영화 내용 분석의 고유값이 너무 큽니다.(영화마다 내용이 다르니 당연하지만)

# 다음의 column들은 결측치가 너무 많으므로 삭제합니다.
# budget, usa_gross_income, worlwide_gross_income, metascore

# 다음의 column들은 추가적인 처리를 하려고 합니다.
# year = 개봉 연도와 평점의 관계를 볼 수 있을듯 합니다.('date_published' column은 확인하니 첫 개봉 일자가 아닌 경우도 많아서 이렇게 처리하겠습니다.)
# genre = 장르가 하나인 경우와 2개 이상인 경우가 서로 섞여 있으므로, 분리해서 확인하고자 합니다.
# duration = 영화 길이는 대부분이 200분 이하이므로, 평균에서 많이 벗어나는 이상치를 제거하거나 '200분 이상' 항목으로 묶어버리겠습니다.
# country = 고유값이 많은데 1/3은 미국이 차지하고 있으므로, 분포를 확인해 '기타 국가' 항목으로 많은 수를 묶겠습니다.
# language = 국가와 마찬가지로 1/3은 영어가 차지하고 있으므로, 분포를 확인해 '기타 언어' 항목으로 많은 수를 묶겠습니다.
# reviews_from_users, reviews_from_critics = total_votes는 숫자 평점을 한 사람 수이고, 위 2 항목은 평론가와 일반인들이 IMDb 사이트에 글로 남긴 평가를 한 숫자입니다.
#                                            글로 남긴 숫자가 많을수록 더 좋은 평점을 받았는지 확인하려고 합니다.
# 삭제되지 않은 column들 중에서 rating과 review에 관계된 column의 결측치는 평균값 등이 아닌 0으로 채웁니다.
# country의 결측치는 '기타 국가'로 처리하겠습니다.
# language의 결측치는 1936년 이후 영화일 경우 country 항목을 보고 제1언어로 채우도록 하겠습니다.(ex. USA -> 영어, Germany -> 독일어) 기타이면 그냥 기타 언어로 처리하겠습니다.
# 1936년 이전에는 무성 영화가 만들어지던 시기였으므로 복잡합니다. 최초 유성 영화인 The Jazz Singer는 1927년도에 나왔으므로 그 이전 영화는 모든 Language를 None으로 처리하겠습니다.
# 27년과 36년 사이 영화는 전부 확인할 수가 없으므로 결측일 경우는 None으로, 아닌 경우에는 값을 그대로 쓰겠습니다.

In [18]:
movierating = movierating.drop(['title', 'original_title', 'date_published', 'director', 'writer', 'production_company',
                                'actors', 'description', 'budget', 'usa_gross_income', 'worlwide_gross_income', 'metascore'], axis=1)

In [19]:
movierating

imdb_title_id  year  ... non_us_voters_rating  non_us_voters_votes
0         tt0000009  1894  ...                  6.0                 70.0
1         tt0000574  1906  ...                  6.2                331.0
2         tt0001892  1911  ...                  5.9                123.0
3         tt0002101  1912  ...                  4.7                105.0
4         tt0002130  1911  ...                  7.0               1166.0
...             ...   ...  ...                  ...                  ...
85850     tt9908390  2020  ...                  5.3                214.0
85851     tt9911196  2020  ...                  7.7                388.0
85852     tt9911774  2019  ...                  2.0                  2.0
85853     tt9914286  2019  ...                  5.8                  5.0
85854     tt9914942  2019  ...                  6.7                 60.0

[85855 rows x 56 columns]